Topic classification with BERTopic

Install transformers 4.41.0 for compatability with spacy and BERTopic

`pip install transformers==4.41.0` 

Careful when running this, very hardware intensive

In [22]:
import pandas as pd
from bertopic import BERTopic
from sentence_transformers import SentenceTransformer
from umap import UMAP
from sklearn.feature_extraction.text import CountVectorizer
import numpy as np
import psutil
import gc
from tqdm import tqdm
import re
import umap

In [23]:
df_posts = pd.read_json('../data/dataset.json')
df_posts.head()

timestamp                                               text     text_id  \
0 2024-10-31  Running a business means juggling countless ad...  2018569761   
1 2024-10-31  Liz Truss is walking in the lingering shadow o...  2092717718   
2 2024-10-31  The UK is bracing for war as government buildi...  2059143248   
3 2024-10-31  Marrying a second or third cousin once removed...  2008209828   
4 2024-10-31  It's truly disgraceful how the Indian National...  2001239278   

               user     user_id  
0     danielwoodard  1077866112  
1  nelsonjacqueline  1089670430  
2           ihooper  1007478642  
3    wrightnicholas  1039258480  
4         michael51  1021455936

Apply minimal preprocessing (Remove URLs and Mentions)

In [24]:
df_posts['text'] = df_posts['text'].apply(lambda x: re.sub(r'http\S+|www\S+|https\S+|@\w+', '', x) if pd.notna(x) else x)

In [25]:
df_posts = df_posts.sample(frac=0.1, random_state=42)  # 10% of the dataset

In [26]:
# Monitor memory usage
def monitor_memory():
    process = psutil.Process()
    memory_gb = process.memory_info().rss / 1024 / 1024 / 1024
    return f"Memory Usage: {memory_gb:.2f} GB"

# Create embeddings with memory monitoring and larger batches
def create_multifeature_embeddings(df_posts, sentence_model, batch_size=64):
    print(f"\nStarting embedding generation for {len(df_posts)} documents")
    print(monitor_memory())

    print("\nGenerating text embeddings...")
    text_embeddings = sentence_model.encode(
        df_posts['text'].fillna("").tolist(),
        batch_size=batch_size,
        show_progress_bar=True
    )
    print(monitor_memory())

    print(monitor_memory())
    return text_embeddings

# Set up and train BERTopic model with memory optimization
def setup_bertopic_model(df_posts, batch_size=64):
    print(f"\nDataset size: {len(df_posts)} documents")
    print(f"DataFrame memory usage: {df_posts.memory_usage().sum() / 1024**2:.2f} MB")
    print(monitor_memory())

    print("\nInitializing models...")
    sentence_model = SentenceTransformer('all-MiniLM-L6-v2')

    vectorizer_model = CountVectorizer(
        stop_words="english",
        min_df = 5,  # Terms must appear in at least 350 rows (0.5% of dataset)
        max_df = 0.5,  # Terms must appear in less than 80% of the dataset (56,000 rows)
        ngram_range=(1, 2) # Bigrams good for tweets
    )

    umap_model = UMAP(
        n_neighbors=5,
        n_components=5,
        min_dist=0.1,
        metric='cosine',
        random_state=42
    )

    embeddings = create_multifeature_embeddings(df_posts, sentence_model, batch_size)

    topic_model = BERTopic(
        embedding_model=sentence_model,
        vectorizer_model=vectorizer_model,
        umap_model=umap_model,
        min_topic_size = 10,      # uncomment to set manual minimum topic size
        nr_topics='auto',
        calculate_probabilities=True,
        verbose=True
    )

    print("\nFitting BERTopic model...")
    topics, probs = topic_model.fit_transform(
        documents=df_posts['text'].fillna("").tolist(),
        embeddings=embeddings
    )

    return topic_model, topics, probs

# Analyze topics with memory considerations
def analyze_topics(topic_model, topics, df_posts):
    print("\nAnalyzing topics...")
    print(monitor_memory())

    topic_info = topic_model.get_topic_info()

    df_posts['topic'] = topics

    topic_docs = {}
    unique_topics = set(topics)
    print(f"\nFound {len(unique_topics)-1} topics (excluding -1)")

    for topic in tqdm(unique_topics):
        if topic != -1:
            topic_docs[topic] = df_posts[df_posts['topic'] == topic]['text'].head(3).tolist()

    try:
        print("\nGenerating visualizations...")
        topic_model.visualize_topics()
        topic_model.visualize_hierarchy()
    except Exception as e:
        print(f"Warning: Visualization error: {e}")

    return topic_info, topic_docs

# Run the complete pipeline with memory monitoring
def run_topic_analysis(df_posts, batch_size=64):
    print(f"Starting analysis with batch size: {batch_size}")
    print(monitor_memory())

    if 'text' not in df_posts.columns:
        raise ValueError("Missing required column: text")

    topic_model, topics, probs = setup_bertopic_model(df_posts, batch_size)
    topic_info, topic_docs = analyze_topics(topic_model, topics, df_posts)

    summary = {
        'num_topics': len(set(topics)) - 1,
        'topic_sizes': topic_info['Count'].tolist(),
        'top_topics': topic_info.head(10).to_dict('records')
    }

    return topic_model, summary, topics, probs

In [27]:
try:
    topic_model, summary, topics, probs = run_topic_analysis(df_posts, batch_size=64)
    
    print(f"\nAnalysis complete!")
    print(f"Found {summary['num_topics']} topics")
    print("\nTop 10 topics:")
    for topic in summary['top_topics']:
        print(f"Topic {topic['Topic']}: Size {topic['Count']}")
    
    topic_model.save("bertopic_model_large")
    
except Exception as e:
    print(f"Error during analysis: {e}")

Starting analysis with batch size: 64
Memory Usage: 0.61 GB

Dataset size: 7026 documents
DataFrame memory usage: 0.32 MB
Memory Usage: 0.61 GB

Initializing models...

Starting embedding generation for 7026 documents
Memory Usage: 0.69 GB

Generating text embeddings...


Batches: 100%|██████████| 110/110 [00:09<00:00, 12.00it/s]
2025-01-26 17:43:28,571 - BERTopic - Dimensionality - Fitting the dimensionality reduction algorithm


Memory Usage: 0.98 GB
Memory Usage: 0.98 GB

Fitting BERTopic model...


2025-01-26 17:43:32,530 - BERTopic - Dimensionality - Completed ✓
2025-01-26 17:43:32,531 - BERTopic - Cluster - Start clustering the reduced embeddings
2025-01-26 17:43:34,985 - BERTopic - Cluster - Completed ✓
2025-01-26 17:43:34,985 - BERTopic - Representation - Extracting topics from clusters using representation models.
2025-01-26 17:43:35,131 - BERTopic - Representation - Completed ✓
2025-01-26 17:43:35,131 - BERTopic - Topic reduction - Reducing number of topics
2025-01-26 17:43:35,249 - BERTopic - Topic reduction - Reduced number of topics from 149 to 11



Analyzing topics...
Memory Usage: 1.16 GB

Found 10 topics (excluding -1)


100%|██████████| 11/11 [00:00<00:00, 6128.77it/s]
2025-01-26 17:43:35,309 - BERTopic - WARNING: When you use `pickle` to save/load a BERTopic model,please make sure that the environments in which you saveand load the model are **exactly** the same. The version of BERTopic,its dependencies, and python need to remain the same.



Generating visualizations...

Analysis complete!
Found 10 topics

Top 10 topics:
Topic -1: Size 2464
Topic 0: Size 4310
Topic 1: Size 109
Topic 2: Size 46
Topic 3: Size 18
Topic 4: Size 16
Topic 5: Size 15
Topic 6: Size 14
Topic 7: Size 12
Topic 8: Size 11


In [28]:
# 1. Save visualizations to HTML files
fig = topic_model.visualize_barchart(top_n_topics=20)
fig.write_html("../output/topic_barchart.html")

topic_model.visualize_topics().write_html("../output/topic_clusters.html")
topic_model.visualize_hierarchy().write_html("../output/topic_hierarchy.html")

# 2. Print text-based summary
topics_info = topic_model.get_topic_info()
print("\nMost frequent topics with their terms:")
for _, row in topics_info.head(20).iterrows():
    topic_id = row['Topic']
    size = row['Count']
    if topic_id != -1:
        terms = topic_model.get_topic(topic_id)
        print(f"\nTopic {topic_id} (Size: {size}):")
        # Print top 10 terms for each topic with their weights
        for term, weight in terms[:20]:
            print(f"  - {term}: {weight:.3f}")


Most frequent topics with their terms:

Topic 0 (Size: 4310):
  - let: 0.082
  - like: 0.079
  - need: 0.073
  - high: 0.071
  - miss: 0.064
  - making: 0.049
  - ve: 0.046
  - help: 0.045
  - education: 0.042
  - data: 0.038

Topic 1 (Size: 109):
  - times: 0.851
  - high: 0.201
  - 24: 0.050
  - service: 0.021
  - 12: 0.019
  - data: 0.015
  - making: 0.010
  - : 0.000
  - : 0.000
  - : 0.000

Topic 2 (Size: 46):
  - help: 0.325
  - contact: 0.215
  - ve: 0.146
  - need: 0.068
  - email: 0.061
  - 24: 0.060
  - check amazing: 0.036
  - education: 0.033
  - problems: 0.033
  - easy: 0.031

Topic 3 (Size: 18):
  - 12: 1.629
  - check amazing: 0.238
  - service: 0.165
  - : 0.000
  - : 0.000
  - : 0.000
  - : 0.000
  - : 0.000
  - : 0.000
  - : 0.000

Topic 4 (Size: 16):
  - email: 0.388
  - 24: 0.287
  - ve: 0.194
  - info: 0.149
  - help: 0.138
  - problems: 0.104
  - service: 0.079
  - contact: 0.076
  - 12: 0.071
  - access: 0.069

Topic 5 (Size: 15):
  - check amazing: 0.309
  - e

In [29]:
from sklearn.datasets import fetch_20newsgroups
from sentence_transformers import SentenceTransformer
from bertopic import BERTopic
from umap import UMAP

# Prepare embeddings
docs = fetch_20newsgroups(subset='all',  remove=('headers', 'footers', 'quotes'))['data']
sentence_model = SentenceTransformer("all-MiniLM-L6-v2")
embeddings = sentence_model.encode(docs, show_progress_bar=False)

# Train BERTopic
#topic_model = BERTopic().fit(docs, embeddings)

# Run the visualization with the original embeddings
topic_model.visualize_documents(docs, embeddings=embeddings)

# Reduce dimensionality of embeddings, this step is optional but much faster to perform iteratively:
reduced_embeddings = UMAP(n_neighbors=10, n_components=2, min_dist=0.0, metric='cosine').fit_transform(embeddings)
topic_model.visualize_documents(docs, reduced_embeddings=reduced_embeddings)


In [30]:
# Transform documents into topics and probabilities
#documents = df_posts['text'].tolist()
#topics, probs = topic_model.transform(documents)

# Reassign "Other" topics to the most probable topic
#import numpy as np
#for i, prob in enumerate(probs):
#    if topics[i] == -1:  # Check for "Other"
#        topics[i] = np.argmax(prob)  # Assign the most probable topic

# Add topic numbers to the dataframe
#df_posts['topic'] = topics

# Generate topic labels
#topic_labels = {}
#for topic_id in set(topics):
#    if topic_id != -1:
#        terms = topic_model.get_topic(topic_id)
#        topic_labels[topic_id] = ", ".join([term for term, _ in terms[:3]])
#    else:
#        topic_labels[topic_id] = "Other"

# Add descriptive topic labels to the dataframe
#df_posts['topic_label'] = df_posts['topic'].map(topic_labels)

# Save augmented dataframe
#df_posts.to_csv('../output/posts_with_topics.csv', index=False)

In [31]:
# Reduce dimensionality of embeddings, this step is optional but much faster to perform iteratively:
reduced_embeddings = UMAP(n_neighbors=10, n_components=2, min_dist=0.0, metric='cosine').fit_transform(embeddings)
topic_model.visualize_documents(docs, reduced_embeddings=reduced_embeddings)
documents = df_posts['text'].tolist()
topics, probs = topic_model.transform(documents)

# Handle "Other" first
num_others = np.sum(np.array(topics) == -1)
for i, prob in enumerate(probs):
    if topics[i] == -1:
        topics[i] = np.argmax(prob)

# Reduce topics to a smaller number for feature clustering
topic_model.reduce_topics(documents, nr_topics=30)

# Generate labels for the topics
topic_labels = {topic_id: ", ".join([term for term, _ in topic_model.get_topic(topic_id)[:3]]) 
               for topic_id in set(topics) if topic_id != -1}
topic_labels[-1] = "Other"

df_posts['topic'] = topics
df_posts['topic_label'] = df_posts['topic'].map(topic_labels)
df_posts.to_csv('../output/posts_with_topics.csv', index=False)

Batches: 100%|██████████| 220/220 [00:09<00:00, 24.37it/s]
2025-01-26 17:45:17,886 - BERTopic - Dimensionality - Reducing dimensionality of input embeddings.
2025-01-26 17:45:18,832 - BERTopic - Dimensionality - Completed ✓
2025-01-26 17:45:18,833 - BERTopic - Clustering - Approximating new points with `hdbscan_model`
2025-01-26 17:45:18,932 - BERTopic - Probabilities - Start calculation of probabilities with HDBSCAN
2025-01-26 17:45:21,550 - BERTopic - Probabilities - Completed ✓
2025-01-26 17:45:21,551 - BERTopic - Cluster - Completed ✓
2025-01-26 17:45:21,559 - BERTopic - Topic reduction - Reducing number of topics
2025-01-26 17:45:21,559 - BERTopic - Topic reduction - Reduced number of topics from 11 to 11


IndexError: index 10 is out of bounds for axis 1 with size 10